# Using Gemini 2.0 Flash to generate the stories
## Using the google SDK with Gemini 2.0 Flash to generate the stories for the english and spanish related images

In [ ]:
from google.colab import drive
import json
import os

# Mount Google Drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!pip install json5

In [ ]:
from PIL import Image
import os
import json5
import time
from google import genai
from google.genai import types
import typing_extensions as typing
from google.colab import userdata


# Schema for the visual storytelling task structured generation
# The Gemini/Gemma model output format will follow this
class StoryPart(typing.TypedDict):
    image: typing.Annotated[int, "Should be the number in order according to the number of images in the input."]
    story_part: typing.Annotated[str, "Should be the generated story for the corresponding image in order."]

class Story(typing.TypedDict):
    story: list[StoryPart]
##########################################

#Images for one-shot examples in english
image_eng_path1 = "/content/drive/MyDrive/Project VIST with LLM/one_shot_examples/english/00.png"
image_eng_path2 = "/content/drive/MyDrive/Project VIST with LLM/one_shot_examples/english/01.png"
image_eng_path3 = "/content/drive/MyDrive/Project VIST with LLM/one_shot_examples/english/02.png"
image_eng_path4 = "/content/drive/MyDrive/Project VIST with LLM/one_shot_examples/english/03.png"
image_eng_path5 = "/content/drive/MyDrive/Project VIST with LLM/one_shot_examples/english/04.png"

image_eng1 = Image.open(image_eng_path1)
image_eng2 = Image.open(image_eng_path2)
image_eng3 = Image.open(image_eng_path3)
image_eng4 = Image.open(image_eng_path4)
image_eng5 = Image.open(image_eng_path5)

#Images for one-shot examples in spanish
image_spa_path1 = "/content/drive/MyDrive/Project VIST with LLM/one_shot_examples/spanish/00.jpg"
image_spa_path2 = "/content/drive/MyDrive/Project VIST with LLM/one_shot_examples/spanish/01.png"
image_spa_path3 = "/content/drive/MyDrive/Project VIST with LLM/one_shot_examples/spanish/02.jpg"
image_spa_path4 = "/content/drive/MyDrive/Project VIST with LLM/one_shot_examples/spanish/03.png"
image_spa_path5 = "/content/drive/MyDrive/Project VIST with LLM/one_shot_examples/spanish/04.jpg"

image_spa1 = Image.open(image_spa_path1)
image_spa2 = Image.open(image_spa_path2)
image_spa3 = Image.open(image_spa_path3)
image_spa4 = Image.open(image_spa_path4)
image_spa5 = Image.open(image_spa_path5)

class GenAIAgent:
    """
    A utility class for interacting with Google's GenAI models,
    handling synchronous generation.
    """

    # Configuration constants
    DEFAULT_FLASH_MODEL_ID = "gemini-2.0-flash"
    DEFAULT_CONCURRENT_INPUT_TOKENS_LIMIT = 8192
    #System Prompt for the model
    ENGLISH_SYSTEM_PROMPT = \
    '''
    You are an expert storyteller. You are not overly verbose in your stories, and you keep them very interesting.
    Your stories need to be in third person, from an external point of view.
    Craft an engaging story based strictly on the following figures presented in order.
    Follow the schema as defined for your output:
    {{
    "story": [
        {
        "image": <int>,
        "story_part": "<str>"
        },
        ...
    ]
    }}
    '''
    SPANISH_SYSTEM_PROMPT = \
    '''
    Eres un narrador experto en español. No eres excesivamente verboso en tus historias y las mantienes muy interesantes.
    Tus historias necesitan ser creadas en tercera persona, desde un punto de vista externo.
    Crea una historia atractiva basada estrictamente en las siguientes imágenes presentadas en orden.
    Sigue el esquema definido para tu respuesta:
    {{
    "story": [
        {
        "image": <int>,
        "story_part": "<str>"
        },
        ...
    ]
    }}
    '''

    # Standard safety configurations
    API_SAFETY_SETTINGS = [
        types.SafetySetting(category="HARM_CATEGORY_HATE_SPEECH", threshold="OFF"),
        types.SafetySetting(category="HARM_CATEGORY_DANGEROUS_CONTENT", threshold="OFF"),
        types.SafetySetting(category="HARM_CATEGORY_SEXUALLY_EXPLICIT", threshold="OFF"),
        types.SafetySetting(category="HARM_CATEGORY_HARASSMENT", threshold="OFF")
    ]

    #User prompt used for the model with each english language task
    LLM_VIST_GEN_USER_ENGLISH_PROMPT = \
    f'''
    You are an expert storyteller. You are not overly verbose in your stories, and you keep them very interesting.
    Your stories need to be in third person, from an external point of view.
    Craft an engaging story based strictly on the following figures presented in order.
    Follow the schema as defined for your output:
    {{
    "story": [
        {{
        "image": <int>,
        "story_part": "<str>"
        }},
        ...
    ]
    }}

    First I will show you an example of how to do it:
    INPUT:
    Image 1:
    {image_eng1}
    Image 2:
    {image_eng2}
    Image 3:
    {image_eng3}
    Image 4:
    {image_eng4}
    Image 5:
    {image_eng5}
    OUTPUT:
    {{
    "story": [
        {{
        "image": 1,
        "story_part": "I am big. I am bigger than a stream. I have lot of water. My water is used for drinking. They say I always run. I never walk. My water moves from here to there. They say I flow."
        }},
        {{
        "image": 2,
        "story_part": "I have a mouth. But I never eat. I can't even talk. You hear the sound when I flow. I move soil and small rocks. I help move logs of wood. I do so much work but I don't have hands."
        }},
        {{
        "image": 3,
        "story_part": "I have a bed. But I don't sleep. I am always awake. I am always moving. I make soil. I make valleys. My water is sweet."
        }},
        {{
        "image": 4,
        "story_part": "Let me tell you again. I have no legs but I can run. I can't eat or talk but I have a mouth. I have a long bed but I never sleep. I have a bank but there is no money in it. Did you guess who am I?"
        }},
        {{
        "image": 5,
        "story_part": "A river! I am a river. Do you know some names I have?"
        }}
    ]
    }}

    Now generate the story for the user's input.

    ----INPUT STARTS HERE----
    '''

    #User prompt used for the model with each english language task
    LLM_VIST_GEN_USER_SPANISH_PROMPT = \
    f'''
    Eres un narrador experto en español. No eres excesivamente verboso en tus historias y las mantienes muy interesantes.
    Tus historias necesitan ser creadas en tercera persona, desde un punto de vista externo.
    Crea una historia atractiva basada estrictamente en las siguientes imágenes presentadas en orden.
    Sigue el esquema definido para tu respuesta:
    {{
    "story": [
        {{
        "image": <int>,
        "story_part": "<str>"
        }},
        ...
    ]
    }}
    Primero te enseñaré un ejemplo sobre como hacerlo:
    INPUT:
    Imagen 1:
    {image_spa1}
    Imagen 2:
    {image_spa2}
    Imagen 3:
    {image_spa3}
    Imagen 4:
    {image_spa4}
    Imagen 5:
    {image_spa5}
    OUTPUT:
    {{
    "story": [
        {{
        "image": 1,
        "story_part": "Ya pasaron varios meses. He crecido mucho últimamente. Creo que ya no quepo aquí en donde me encuentro.  Mi mami ya sabe cuando naceré. Creo que será ¡hoy! es ¡hoy!, es ¡hoy!Por fin conoceré a mamá y a papá. ¿Cómo serán? ¿Me querrán como yo los quiero?¿Será que ellos van a jugar conmigo? Tengo tantas preguntas. Ya estoy feliz pensando en estar con ellos siempre."
        }},
        {{
        "image": 2,
        "story_part": "Mi papá estaba angustiado en la sala de espera. No le daban noticias de mi nacimiento. El médico llega y le cuenta que soy un hermoso bebé.\nLe pide que se coloque una bata para entrar a conocerme. Al verme, papá llora de felicidad.\nYo sé que mi mamá es una guerrera. Ella siempre luchará por mí.  Me va a proteger toda la vida. Me va a alimentar y resguardar de todo peligro. Ya quiero estar en casa y conocer todo lo que me tienen preparado."
        }},
        {{
        "image": 3,
        "story_part": "Las mamás son muy dulces. Siempre saben qué es lo mejor para ti. Cuando estás en un problema, siempre te acompañan. Mamá siempre se preocupa cuando estás lejos. Le pide a Dios que te proteja.\n\n Papá siempre está con ella apoyándola. Juntos quieren verte crecer y que te conviertas en una persona de bien. Quieren que estudies y tengas un buen futuro."
        }},
        {{
        "image": 4,
        "story_part": "Papá y mamá son personas increíbles. Son como ángeles que nos cuidan sin importar la edad que tengamos. Si somos bebés, niños, adolescentes o personas adultas, siempre están para apoyarnos.\nCuando pase el tiempo y ellos envejezcan, debo cuidar de ellos, así como ellos cuidaron de mí.  Me enseñaron a caminar, a amarrarme las agujetas de los zapatos, a aprender, a ser feliz y a vivir en paz.\nMis papás son lo mejor que he tenido.  Siempre los llevo y llevaré en mi corazón. ¡Somos una hermosa familia!"
        }},
        {{
        "image": 5,
        "story_part": "¡Mi familia!"
        }}
    ]
    }}

    Ahora genera la historia para el input del usuario.
    IMPORTANTE: El output debe estar en idioma español.

    ----EL INPUT EMPIEZA AQUí----
    '''

    def __init__(
        self,
        specified_model_id: str = None,
        select_system_prompt: str = None,
    ):
        """
        Initializes the GenAIAgent with model and system prompt settings.

        Args:
            specified_model_id (str, optional): The ID of the model to use.
                                              Defaults to DEFAULT_FLASH_MODEL_ID.
            custom_system_prompt (str, optional): A custom system instruction.
                                                Defaults to DEFAULT_SYSTEM_PROMPT.
            api_key (str, optional): Your Google API key. If None, it will attempt
                                     to use the key passed during client initialization
                                     (e.g., via genai.configure or environment variable).
        """
        self.chosen_model_id = specified_model_id or self.DEFAULT_FLASH_MODEL_ID
        if select_system_prompt:
            if select_system_prompt == "Spanish":
                self.active_system_prompt = self.SPANISH_SYSTEM_PROMPT
                self.active_user_prompt = self.LLM_VIST_GEN_USER_SPANISH_PROMPT
            else:
                self.active_system_prompt = self.ENGLISH_SYSTEM_PROMPT
                self.active_user_prompt = self.LLM_VIST_GEN_USER_ENGLISH_PROMPT
        else:
            self.active_system_prompt = self.ENGLISH_SYSTEM_PROMPT
            self.active_user_prompt = self.LLM_VIST_GEN_USER_ENGLISH_PROMPT


        api_key = userdata.get("GOOGLE_API_KEY")

        self.genai_client = genai.Client(api_key=api_key) # Client for generation

        self.output_token_cap = 8192 # Maximum tokens for model response

    def generate_single_response(
        self,
        input_content_list: list,
        response_schema_definition,
        include_metrics_log: bool = False
    ):
        """
        Generates a single content response from the model.
        """
        request_start_time = time.time()
        if(self.chosen_model_id=="gemini-2.0-flash"):
            content_generation_config = types.GenerateContentConfig(
                temperature=1,
                system_instruction=self.active_system_prompt,
                max_output_tokens=self.output_token_cap,
                response_modalities=["TEXT"],
                response_mime_type = "application/json",
                response_schema = response_schema_definition,
                safety_settings=self.API_SAFETY_SETTINGS
            )
        #Gemma 3 with the API does not support structured output or System Prompt
        else:
            content_generation_config = types.GenerateContentConfig(
                temperature=1,
                max_output_tokens=self.output_token_cap,
                response_modalities=["TEXT"],
                safety_settings=self.API_SAFETY_SETTINGS
            )

        api_response = self.genai_client.models.generate_content(
            model=self.chosen_model_id,
            contents=input_content_list,
            config=content_generation_config,
        )

        generated_text = api_response.text
        if include_metrics_log:
            performance_log = {
                "model_used": self.chosen_model_id,
                "output_tokens": api_response.usage_metadata.candidates_token_count,
                "input_tokens": api_response.usage_metadata.prompt_token_count,
                "elapsed_time_sec": round(time.time() - request_start_time, 2),
            }
            return generated_text, performance_log
        return generated_text

In [ ]:
# LLM Logic
def generate_story_with_llm(image_data_list, llm_model_name, language):
    """
    Function to generate a story using an LLM.
    Returns a list of story segments, one for each image.

    Args:
        image_data_list (list): A list of image data (e.g., bytes).
        llm_model_name (str): The name of the selected LLM.
        language (str): The selected language ("English" or "Spanish").

    Returns:
        list[str]: A list of story segments, or an empty list/error indication.
    """
    num_images = len(image_data_list)
    story_segments = []
    model_name = ""
    if llm_model_name == "Gemma 3 (27B)":
        model_name = "gemma-3-27b-it"
    else:
        model_name = "gemini-2.0-flash"

    # Instance of the agent for story generation
    ai_handler = GenAIAgent(specified_model_id=model_name, select_system_prompt=language)
    # Story generation logic
    if num_images > 0:
        user_content = [ai_handler.active_user_prompt]
        for i, image in enumerate(image_data_list):
            if language == "Spanish":
                user_content.append(f"Imagen {i+1}:")
            else:
                user_content.append(f"Image {i+1}:")
            user_content.append(image)

    schema = Story
    gen_story, log = ai_handler.generate_single_response(input_content_list=user_content, response_schema_definition=schema, include_metrics_log = True)

    text = gen_story.replace("```json","")
    text = text.replace("```","")
    print(gen_story)
    final_story = json5.loads(text)
    print(final_story)
    print("Generation successful!")
    print(log)
    for part in final_story["story"]:
        story_segments.append(part["story_part"])
    return story_segments, log

In [ ]:
with open("/content/drive/MyDrive/Project VIST with LLM/filtered_dataset_with_imgs_path_english.json", "r", encoding="utf-8") as f:
  norm_stories_eng = json.load(f)

In [ ]:
norm_stories_eng

[{'album_id': 'f95e07f0-a0a0-4cd2-8db2-fa9823f68b30',
  'texts': ['"Father, Father!"\xa0I called. "Where are you?"\xa0 There was no answer. I sat helpless, wondering where he had gone.\n\nThen sticks and leaves crackled. I imagined a dark figure coming towards me.',
   'Maybe it was the old man with false teeth who grinned as he ate people!\n\n"Go away! Go away!" I cried.\nThen I heard a dog barking. It was getting closer and closer.',
   '"Help, Help! Someone help me!" I yelled. The crackling of leaves was getting closer and closer. Then, jumping and licking me, was Haffen, my pet dog.\n"Haffen! Haffen! You’ve found me," I cried.\n"Woof! Woof!" Haffen barked. He ran ahead of me. I couldn\'t see, only feel with my hands. I bumped into a tree root and fell over. I stepped into a thorn bush and cried as it pricked me. The darkness seemed endless. Haffen ran back and forth barking to keep me walking. But I could not move any further. I felt as if I had been swallowed up by the darkness.',

In [ ]:
with open("/content/drive/MyDrive/Project VIST with LLM/filtered_dataset_with_imgs_path_spanish.json", "r", encoding="utf-8") as f:
  norm_stories_spa = json.load(f)

## Processing english related images in the dataset

In [ ]:
from PIL import Image
from tqdm import tqdm
import time
from pathlib import Path

llm_model_name = "Gemini 2.0 Flash" #"Gemma 3 (27B)"
language = "English"
path_results = "/content/drive/MyDrive/Project VIST with LLM/results/results_gemini20_eng.json"
json_path_results = Path(path_results)
path_logs = "/content/drive/MyDrive/Project VIST with LLM/results/logs_gemini20_eng.json"
json_path_logs = Path(path_logs)

results = {}
logs = []
log_bundle = {}
count = 1
start_time = time.time()

for story_eng in tqdm(norm_stories_eng):
  if json_path_results.exists():
    with open(json_path_results, "r", encoding="utf-8") as f:
        results_processed = json.load(f)
  else:
    results_processed = []
  if json_path_logs.exists():
    with open(json_path_logs, "r", encoding="utf-8") as f:
        logs = json.load(f)
  else:
    logs = []

  already_processed = [entry["album_id"] for entry in results_processed]
  current_album_id  = story_eng.get("album_id")
  if current_album_id in already_processed:
    continue
  print(already_processed)

  images_list = story_eng.get("images")
  images_for_llm = []
  for image_path in images_list:
    images_for_llm.append(Image.open(image_path))

  gen_story, log = generate_story_with_llm(images_for_llm, llm_model_name, language)

  if((count%10) == 0): #there is an API limit of only 10 API calls per minute for gemini 2.0 flash, so gotta validate we are not violating that
      time_taken = time.time() - start_time
      while (time_taken < 60):
          time.sleep(61-time_taken)
          time_taken = time.time() - start_time
      start_time = time.time()

  if(len(story_eng.get("texts")) == len(gen_story)):
    results["album_id"] = story_eng.get("album_id")
    results["texts"] = story_eng.get("texts")
    results["images"] = story_eng.get("images")
    results["predicted_texts"] = gen_story
    results_processed.append(results) #appending all the fields of final results for each story

    log_bundle[f"album_id"] = story_eng.get("album_id")
    log_bundle[f"log"] = log #saving the logs
    logs.append(log_bundle)

    # Saving all to not lose progress by an external error
    # Save results to a JSON file
    with open(json_path_results, "w", encoding="utf-8") as f:
        json.dump(results_processed, f, indent=2, ensure_ascii=False)

    # Save logs (a list of log_bundle dicts) to a separate JSON file
    with open(json_path_logs, "w", encoding="utf-8") as f:
        json.dump(logs, f, indent=2, ensure_ascii=False)
    print("Files Successfully saved!")

  count+=1

  0%|          | 0/479 [00:00<?, ?it/s]

[]


  0%|          | 1/479 [00:12<1:38:24, 12.35s/it]

{
    "story": [
        {
            "image": 1,
            "story_part": "A young boy was walking through the forest one night, when he heard a loud and eerie howl. It sent chills down his spine."
        },
        {
            "image": 2,
            "story_part": "He ran and ran until he encountered a horrible looking creature! The creature had long nails and yellow teeth."
        },
        {
            "image": 3,
            "story_part": "The boy's luck turned for the worst when a large wolf appeared. The boy was trapped!"
        },
        {
            "image": 4,
            "story_part": "Just when the wolf was about to attack, the boy's parents emerged from the darkness with torches, scaring away both the wolf and the creature. The boy ran into his parents' arms, relieved to be safe."
        }
    ]
}
{'story': [{'image': 1, 'story_part': 'A young boy was walking through the forest one night, when he heard a loud and eerie howl. It sent chills down his spine.'}, {'

  0%|          | 2/479 [00:21<1:24:40, 10.65s/it]

...

{
    "story": [
        {
            "image": 1,
            "story_part": "The teacher pointed towards the window, her expression stern. \"Who started that fire?\" she demanded, her eyes scanning the line of students. A plume of smoke billowed in the distance, a clear sign of mischief gone awry."
        },
        {
            "image": 2,
            "story_part": "Outside, the teacher confronted three students huddled around a small, smoldering fire. Charred sticks lay scattered around the flames, evidence of their playful arson. \"Explain yourselves,\" she said, her voice laced with disappointment."
        },
        {
            "image": 3,
            "story_part": "The students looked down, shamefaced. They had been roasting corn, a harmless activity that had quickly spiraled out of control. \"We didn't mean for it to get so big,\" one of them mumbled, offering a half-eaten cob as a peace offering."
        }
    ]
}
{'story': [{'image': 1, 'story_part': 'The teacher pointe

100%|█████████▉| 478/479 [1:13:30<00:06,  6.98s/it]

{
    "story": [
        {
            "image": 1,
            "story_part": "The wealthy man walked past the poor man and his dog, seemingly unaffected by their plight. The poor man reached out a hand, a silent plea for help."
        },
        {
            "image": 2,
            "story_part": "Later, the wealthy man met with an associate and shook his hand, sealing a deal that would bring even more wealth. The irony was stark: one man's fortune built on the backs of others."
        }
    ]
}
{'story': [{'image': 1, 'story_part': 'The wealthy man walked past the poor man and his dog, seemingly unaffected by their plight. The poor man reached out a hand, a silent plea for help.'}, {'image': 2, 'story_part': "Later, the wealthy man met with an associate and shook his hand, sealing a deal that would bring even more wealth. The irony was stark: one man's fortune built on the backs of others."}]}
Generation successful!
{'model_used': 'gemini-2.0-flash', 'output_tokens': 129, 'input_tok

100%|██████████| 479/479 [1:13:38<00:00,  9.22s/it]

{
    "story": [
        {
            "image": 1,
            "story_part": "In the realm of celestial wonders, an angel soared amidst a tapestry of twinkling stars. Its radiant wings carried it through the vast expanse, a beacon of hope in the inky darkness."
        },
        {
            "image": 2,
            "story_part": "Far below, a young girl gazed up at the sky, her eyes filled with dreams as she watched birds dance among fluffy clouds. A silver airplane streaked across the azure canvas, sparking her imagination with thoughts of far-off lands and boundless adventures."
        }
    ]
}
{'story': [{'image': 1, 'story_part': 'In the realm of celestial wonders, an angel soared amidst a tapestry of twinkling stars. Its radiant wings carried it through the vast expanse, a beacon of hope in the inky darkness.'}, {'image': 2, 'story_part': 'Far below, a young girl gazed up at the sky, her eyes filled with dreams as she watched birds dance among fluffy clouds. A silver airplane 

## Processing spanish related images in the dataset

In [ ]:
from PIL import Image
from tqdm import tqdm
import time
from pathlib import Path

llm_model_name = "Gemini 2.0 Flash"
language = "Spanish"
path_results = "/content/drive/MyDrive/Project VIST with LLM/results/results_gemini20_spa.json"
json_path_results = Path(path_results)
path_logs = "/content/drive/MyDrive/Project VIST with LLM/results/logs_gemini20_spa.json"
json_path_logs = Path(path_logs)

results = {}
logs = []
log_bundle = {}
count = 1
start_time = time.time()

for story_spa in tqdm(norm_stories_spa):
  if json_path_results.exists():
    with open(json_path_results, "r", encoding="utf-8") as f:
        results_processed = json.load(f)
  else:
    results_processed = []
  if json_path_logs.exists():
    with open(json_path_logs, "r", encoding="utf-8") as f:
        logs = json.load(f)
  else:
    logs = []

  already_processed = [entry["album_id"] for entry in results_processed]
  current_album_id  = story_spa.get("album_id")
  if current_album_id in already_processed:
    continue
  print(already_processed)

  images_list = story_spa.get("images")
  images_for_llm = []
  for image_path in images_list:
    images_for_llm.append(Image.open(image_path))

  gen_story, log = generate_story_with_llm(images_for_llm, llm_model_name, language)

  if((count%10) == 0): #there is an API limit of only 10 API calls per minute for gemini 2.0 flash, so gotta validate we are not violating that
      time_taken = time.time() - start_time
      while (time_taken < 60):
          time.sleep(61-time_taken)
          time_taken = time.time() - start_time
      start_time = time.time()

  if(len(story_spa.get("texts")) == len(gen_story)):
    results["album_id"] = story_spa.get("album_id")
    results["texts"] = story_spa.get("texts")
    results["images"] = story_spa.get("images")
    results["predicted_texts"] = gen_story
    results_processed.append(results) #appending all the fields of final results for each story

    log_bundle[f"album_id"] = story_spa.get("album_id")
    log_bundle[f"log"] = log #saving the logs
    logs.append(log_bundle)

    # Saving all to not lose progress by an external error
    # Save results to a JSON file
    with open(json_path_results, "w", encoding="utf-8") as f:
        json.dump(results_processed, f, indent=2, ensure_ascii=False)

    # Save logs (a list of log_bundle dicts) to a separate JSON file
    with open(json_path_logs, "w", encoding="utf-8") as f:
        json.dump(logs, f, indent=2, ensure_ascii=False)
    print("Files Successfully saved!")

  count+=1

  0%|          | 0/128 [00:00<?, ?it/s]

['dd4c4d9e-9f6a-45ba-9867-cdbe7b9774e2', '7ba4a4c0-23d7-494b-96f7-f8f8137e3ca6', 'e7fb2a5c-e8d5-47a8-afa1-01455302f4a4']


  3%|▎         | 4/128 [00:02<01:27,  1.42it/s]

{
    "story": [
        {
            "image": 1,
            "story_part": "En un pintoresco pueblo, donde las casas se visten de colores y el sol siempre sonríe, vivía un niño llamado Mateo. Le encantaba explorar cada rincón, con los brazos abiertos, como si quisiera abrazar el mundo entero."
        },
        {
            "image": 2,
            "story_part": "Un día, mientras jugaba cerca de la plaza principal, Mateo conoció a Sofía, una niña de ojos brillantes y una sonrisa contagiosa. Juntos, descubrieron la belleza de su pueblo, corriendo entre la fuente y la iglesia, soñando con aventuras."
        }
    ]
}
{'story': [{'image': 1, 'story_part': 'En un pintoresco pueblo, donde las casas se visten de colores y el sol siempre sonríe, vivía un niño llamado Mateo. Le encantaba explorar cada rincón, con los brazos abiertos, como si quisiera abrazar el mundo entero.'}, {'image': 2, 'story_part': 'Un día, mientras jugaba cerca de la plaza principal, Mateo conoció a Sofía, una niña 

  4%|▍         | 5/128 [00:09<04:49,  2.35s/it]

...

{
  "story": [
    {
      "image": 1,
      "story_part": "Tres pequeños aventureros exploraban una cueva rocosa. El primero, con una gorra verde, parecía nervioso, mirando a su alrededor con inquietud. El segundo, vestido de azul, compartía su preocupación, con los ojos bien abiertos. El tercero, el más osado con su sombrero amarillo, sonreía mientras señalaba un extraño objeto roto en el suelo: una especie de paraguas de colores verde y rojo."
    },
    {
      "image": 2,
      "story_part": "El niño del sombrero amarillo se acercó con curiosidad al paraguas roto, examinándolo de cerca. Los otros dos permanecieron cautelosos, observando desde la distancia. ¿Qué secretos ocultaba aquella cueva? ¿Y cómo había llegado ese extraño objeto allí?"
    }
  ]
}
{'story': [{'image': 1, 'story_part': 'Tres pequeños aventureros exploraban una cueva rocosa. El primero, con una gorra verde, parecía nervioso, mirando a su alrededor con inquietud. El segundo, vestido de azul, compartía su preocup

 99%|█████████▉| 127/128 [14:34<00:05,  5.37s/it]

{
  "story": [
    {
      "image": 1,
      "story_part": "En la densa jungla, una pequeña lagartija llamada Verde se estiraba sobre una hoja. Verde no era una lagartija común; soñaba con aventuras más allá de su rama. Ansiaba explorar el mundo, pero temía lo desconocido."
    },
    {
      "image": 2,
      "story_part": "Un día, mientras Verde contemplaba el horizonte, vio a una anciana en un jardín exuberante. La mujer, con una sonrisa serena, parecía irradiar una paz que Verde nunca había sentido. Intrigado, Verde decidió que debía conocerla."
    }
  ]
}
{'story': [{'image': 1, 'story_part': 'En la densa jungla, una pequeña lagartija llamada Verde se estiraba sobre una hoja. Verde no era una lagartija común; soñaba con aventuras más allá de su rama. Ansiaba explorar el mundo, pero temía lo desconocido.'}, {'image': 2, 'story_part': 'Un día, mientras Verde contemplaba el horizonte, vio a una anciana en un jardín exuberante. La mujer, con una sonrisa serena, parecía irradiar una p

100%|██████████| 128/128 [14:44<00:00,  6.91s/it]

{
"story": [
{
"image": 1,
"story_part": "Un campesino intenta reparar la cerca de su granja, pero su pequeño perro parece oponerse, ladrando y saltando a su alrededor mientras el hombre intenta clavar un poste. La tarea se vuelve más difícil con la insistencia del can."
},
{
"image": 2,
"story_part": "Dos mujeres, vestidas con atuendos tradicionales, observan el paisaje montañoso. La mayor parece preocupada, mientras que la más joven mantiene una actitud más serena, como si rezara en silencio."
},
{
"image": 3,
"story_part": "La joven le ofrece el perro al señora mayor. La mujer joven intenta consolar a la anciana, quizás buscando aliviar su tristeza con la compañía del animal."
},
{
"image": 4,
"story_part": "De repente, un grupo de cerdos se escapa, causando revuelo en la granja. Las mujeres intentan desesperadamente detenerlos, mientras el perro se une a la persecución, ladrando y corriendo tras los animales."
},
{
"image": 5,
"story_part": "Finalmente, las mujeres logran controlar

In [ ]:
!pip install nltk bert-score matplotlib

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.1/61.1 kB 2.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 1.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 5.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 8.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 26.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 1.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 11.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 9.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 5.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 42.2 MB/s eta 0:00:00
  Attempting uninstall: nvidia-nvjitlink-cu12
    Found existing installation: nvidia-nvjitlink-cu12 12.5.82
    Uninstalling n

In [ ]:
# Checking the final length for the generated stories, I skipped the stories with None generation
with open("/content/drive/MyDrive/Project VIST with LLM/results/results_gemini20_eng.json", "r", encoding="utf-8") as f:
  res_gem_20_eng = json.load(f)
with open("/content/drive/MyDrive/Project VIST with LLM/results/results_gemini20_spa.json", "r", encoding="utf-8") as f:
  res_gem_20_spa = json.load(f)

with open("/content/drive/MyDrive/Project VIST with LLM/results/results_gemma3_eng.json", "r", encoding="utf-8") as f:
  res_gemma_3_eng = json.load(f)
with open("/content/drive/MyDrive/Project VIST with LLM/results/results_gemma3_spa.json", "r", encoding="utf-8") as f:
  res_gemma_3_spa = json.load(f)

print("Gemini 2.0 Flash English Results Size", len(res_gem_20_eng))
print("Gemini 2.0 Flash Spanish Results Size", len(res_gem_20_spa))
print("Gemma 3 English Results Size", len(res_gemma_3_eng))
print("Gemma 3 Spanish Results Size", len(res_gemma_3_spa))

Gemini 2.0 Flash English Results Size 473
Gemini 2.0 Flash Spanish Results Size 127
Gemma 3 English Results Size 455
Gemma 3 Spanish Results Size 112
